In [1]:
# SCRIPT: classifier.ipynb
# CREATED BY: Corinne Darche
# PURPOSE: This script preprocesses the audio files, extracts the features, then runs the data through 
# an SVM and a GMM classifier

In [2]:
import numpy as np
import os
import librosa
import pickle
import joblib

from sklearn.utils import shuffle
from sklearn import svm
from sklearn.linear_model import SGDClassifier
from sklearn.mixture import GaussianMixture
from sklearn.cluster import KMeans
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.model_selection import cross_val_score, cross_validate, KFold

In [78]:
# Import all the audio files (TAKES A VERY LONG TIME)
rapFiles = os.listdir("audioset-processing-master/output/rapping")
# This is often a cause of errors and appears randomly, so always check just in case
if '.DS_Store' in rapFiles:
    rapFiles.remove('.DS_Store')
rapPathNames = ["audioset-processing-master/output/rapping/" + file for file in rapFiles]

rapAudio = []
rapSR = []
for path in rapPathNames:
    y, sr = librosa.load(path, mono=True)
    rapAudio.append(y)
    rapSR.append(sr)

chantFiles = os.listdir("/Volumes/CORINNE HARD DRIVE/chantData")
if '.DS_Store' in chantFiles:
    chantFiles.remove('.DS_Store')
chantPathNames = ["/Volumes/CORINNE HARD DRIVE/chantData/" + file for file in chantFiles]

chantAudio = []
chantSR = []
for path in chantPathNames:
    y, sr = librosa.load(path, mono=True)
    chantAudio.append(y)
    chantSR.append(sr)

In [79]:
def vocal_separator(y, sr):
    # FUNCTION: vocal_separator
    # Inspired by the "Vocal separator" in the librosa documentation, this separates vocals from their background
    # Part of preprocessing before features are extracted
    S_mag, S_phase = librosa.magphase(librosa.stft(y))
    S_filter = librosa.decompose.nn_filter(S_mag, 
                                           aggregate=np.median, 
                                           metric='cosine', 
                                           width=int(librosa.time_to_frames(2, sr=sr)))
    
    S_filter = np.minimum(S_mag, S_filter)
    margin_i, margin_v = 2, 10
    power = 2
    
    mask_i = librosa.util.softmask(S_filter, 
                                   margin_i * (S_mag - S_filter), 
                                   power=power)
    
    mask_v = librosa.util.softmask(S_mag - S_filter, 
                                   margin_v * S_filter, 
                                   power=power)
    
    S_foreground = mask_v * S_mag
    S_background = mask_i * S_mag
    
    y_foreground = librosa.istft(S_foreground * S_phase)
    
    return y_foreground

In [83]:
# Extract vocals
chant = []
rap = []

for i in range(0,len(rapAudio)):
    filtered = vocal_separator(rapAudio[i], rapSR[i])
    rap.append(filtered)
    
for j in range(0,len(chantAudio)):
    filtered = vocal_separator(chantAudio[j], chantSR[j])
    chant.append(filtered)

In [86]:
# Feature Extraction
def feature_extraction(audio, sr):
    # Chroma
    chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
    # Spectral centroid
    centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
    # Spectral bandwidth
    bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
    # Spectral flatness
    flatness = np.mean(librosa.feature.spectral_flatness(audio))
    # Spectral rolloff
    rolloff = np.mean(librosa.feature.spectral_rolloff(audio, sr=sr))
    # MFCCs
    mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
    # RMS
    rms = np.mean(librosa.feature.rms(y=audio))
    # Zero-crossing Rate
    zero = np.mean(librosa.feature.zero_crossing_rate(y=audio))
    # Tempogram (rhythm)
    tempogram = np.mean(librosa.feature.tempogram(y=audio, sr=sr))
    return [chroma, centroid, bandwidth, flatness, rolloff, mfcc, rms, tempogram, zero]

In [87]:
# Perform feature extraction 
chantY = np.full((len(chant), 1), 'chant')
rapY = np.full((len(rap), 1), 'rap')

chantX = np.empty((len(chant), 9), dtype=object)
rapX = np.empty((len(rap), 9),dtype=object)

for i in range(0,len(chant)):
    features = feature_extraction(chant[i], chantSR[i])
    for j in range(0,len(features)):
        chantX[i][j] = features[j]
    
for i in range(0,len(rap)):
    features = feature_extraction(rap[i], rapSR[i])
    for j in range(0,len(features)):
        rapX[i][j] = features[j]

<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[0.         0.         0.         ... 0.02574266 0.02254947 0.02543341] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[0.         0.         0.         ... 0.02574266 0.02254947 0.02543341] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[0.         0.         0.         ... 0.02574266 0.02254947 0.02543341] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[0.         0.         0.         ... 0.02574266 0.02254947 

<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[ 6.6724536e-04  1.3894945e-03  1.7899827e-03 ... -1.2302154e-04
  3.8775841e-05 -7.0114271e-05] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[ 6.6724536e-04  1.3894945e-03  1.7899827e-03 ... -1.2302154e-04
  3.8775841e-05 -7.0114271e-05] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[ 6.6724536e-04  1.3894945e-03  1.7899827e-03 ... -1.2302154e-04
  3.8775841e-05 -7.0114271e-05] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
<ipython-input-86-b970aae69294>:10: FutureW

<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[-0.00122438 -0.00125061 -0.00124885 ... -0.07613523 -0.06948169
 -0.06608759] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[-0.00122438 -0.00125061 -0.00124885 ... -0.07613523 -0.06948169
 -0.06608759] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[-0.00122438 -0.00125061 -0.00124885 ... -0.07613523 -0.06948169
 -0.06608759] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[-0.00122438 -0.00125061 -0.00124885 ..

<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[2.58480432e-04 4.29842694e-05 1.18363685e-04 ... 3.04496437e-02
 3.15623879e-02 7.89724011e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[2.58480432e-04 4.29842694e-05 1.18363685e-04 ... 3.04496437e-02
 3.15623879e-02 7.89724011e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[2.58480432e-04 4.29842694e-05 1.18363685e-04 ... 3.04496437e-02
 3.15623879e-02 7.89724011e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
<ipython-input-86-b970aae69294>:10: FutureW

<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[-0.00431091  0.00030638  0.00580004 ...  0.00632155  0.00369524
  0.00126786] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[-0.00431091  0.00030638  0.00580004 ...  0.00632155  0.00369524
  0.00126786] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[-0.00431091  0.00030638  0.00580004 ...  0.00632155  0.00369524
  0.00126786] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  bandwidth = np.mean(librosa.feature.spectral_bandwidth(audio, sr=sr))
<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[-0.00431091  0.00030638  0.00580004 ..

...

<ipython-input-86-b970aae69294>:14: FutureWarning: Pass y=[ 0.00928929 -0.01214748 -0.00200318 ... -0.10999443 -0.12442517
 -0.13998248] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[ 0.122242    0.0534765   0.10000267 ... -0.04596662 -0.03335344
 -0.02231261] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  chroma = np.mean(librosa.feature.chroma_stft(audio, sr=sr))
<ipython-input-86-b970aae69294>:6: FutureWarning: Pass y=[ 0.122242    0.0534765   0.10000267 ... -0.04596662 -0.03335344
 -0.02231261] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  centroid = np.mean(librosa.feature.spectral_centroid(audio, sr=sr))
<ipython-input-86-b970aae69294>:8: FutureWarning: Pass y=[ 0.122242    0.0534765   0.10000267 ... -0.04596662 -0.03

<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[ 1.1694821e-02 -5.7475981e-03 -7.0230121e-06 ...  3.7613965e-03
  4.0379702e-03  3.0510873e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  flatness = np.mean(librosa.feature.spectral_flatness(audio))
<ipython-input-86-b970aae69294>:12: FutureWarning: Pass y=[ 1.1694821e-02 -5.7475981e-03 -7.0230121e-06 ...  3.7613965e-03
  4.0379702e-03  3.0510873e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  rolloff = np.mean(librosa.feature.spectral_rolloff(audio, sr=sr))
<ipython-input-86-b970aae69294>:14: FutureWarning: Pass y=[ 1.1694821e-02 -5.7475981e-03 -7.0230121e-06 ...  3.7613965e-03
  4.0379702e-03  3.0510873e-03] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[-0

<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[-0.08633737 -0.10298782 -0.09923293 ...  0.          0.
  0.        ] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  flatness = np.mean(librosa.feature.spectral_flatness(audio))
<ipython-input-86-b970aae69294>:12: FutureWarning: Pass y=[-0.08633737 -0.10298782 -0.09923293 ...  0.          0.
  0.        ] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  rolloff = np.mean(librosa.feature.spectral_rolloff(audio, sr=sr))
<ipython-input-86-b970aae69294>:14: FutureWarning: Pass y=[-0.08633737 -0.10298782 -0.09923293 ...  0.          0.
  0.        ] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[ 0.03857335  0.00330999  0.01382253 ...  0.00082902  0.00710961
 -0.00251264] as

<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[-0.00048269 -0.00133828 -0.00245823 ...  0.00758742  0.00700723
  0.00614155] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  flatness = np.mean(librosa.feature.spectral_flatness(audio))
<ipython-input-86-b970aae69294>:12: FutureWarning: Pass y=[-0.00048269 -0.00133828 -0.00245823 ...  0.00758742  0.00700723
  0.00614155] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  rolloff = np.mean(librosa.feature.spectral_rolloff(audio, sr=sr))
<ipython-input-86-b970aae69294>:14: FutureWarning: Pass y=[-0.00048269 -0.00133828 -0.00245823 ...  0.00758742  0.00700723
  0.00614155] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[-0.03003284  0.01240461 -0.00621137 ...  0.00178664 -0.0

<ipython-input-86-b970aae69294>:10: FutureWarning: Pass y=[-0.00746373 -0.00184792  0.0019538  ... -0.03273018 -0.02211047
 -0.02711905] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  flatness = np.mean(librosa.feature.spectral_flatness(audio))
<ipython-input-86-b970aae69294>:12: FutureWarning: Pass y=[-0.00746373 -0.00184792  0.0019538  ... -0.03273018 -0.02211047
 -0.02711905] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  rolloff = np.mean(librosa.feature.spectral_rolloff(audio, sr=sr))
<ipython-input-86-b970aae69294>:14: FutureWarning: Pass y=[-0.00746373 -0.00184792  0.0019538  ... -0.03273018 -0.02211047
 -0.02711905] as keyword args. From version 0.10 passing these as positional arguments will result in an error
  mfcc = np.mean(librosa.feature.mfcc(audio, sr=sr))
<ipython-input-86-b970aae69294>:4: FutureWarning: Pass y=[-0.00594589  0.00738259  0.00682235 ...  0.03229498  0.0

In [88]:
# Gather the formatted data
X = np.concatenate((rapX, chantX), axis=0)
y = np.concatenate((rapY, chantY), axis=0)

# Export data so that we don't have to repeat the previous steps every time
np.save('X.npy', X)
np.save('y.npy', y)

In [3]:
# Start here for testing!
X = np.load('X.npy', allow_pickle=True)
y = np.load('y.npy', allow_pickle=True)

In [4]:
# Standard scaler
y = np.ravel(y)
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=0, test_size=0.2)

# Scaling for GMM
scaler = StandardScaler()
scaler = scaler.fit(X_train)
X_train = scaler.transform(X_train)
X_test = scaler.transform(X_test)

# Scaling for SVM
scalerSVM = StandardScaler()
scalerSVM = scalerSVM.fit(X)
X = scalerSVM.transform(X)

In [11]:
SVM = SGDClassifier(loss='hinge',max_iter=1000)
kfold = KFold(n_splits=10)
#resultsSVM = cross_val_score(SVM, X, y, cv=10, scoring='accuracy') 
X, y = shuffle(X, y)
resultsSVM = [SVM.fit(X[train], y[train]).score(X[test], y[test]) for train, test in kfold.split(X)]

print("SVM average accuracy: " + str((sum(resultsSVM) / len(resultsSVM)) * 100))
print("SVM feature coefficients: " + str(SVM.coef_))

SVM average accuracy: 97.64166160175792
SVM feature coefficients: [[0.340345 -8.697448 -2.655002 -0.154642 9.425712 3.662004 0.235018
  -0.601351 4.658937]]


In [10]:
gmm = GaussianMixture(n_components=2, random_state=0, n_init=10, init_params='kmeans', covariance_type='tied')
gmm = gmm.fit(X_train)

results = gmm.predict(X_test)
np.set_printoptions(formatter={'float_kind':'{:f}'.format})

# Calculate score where 1 is chant and 0 is rap

scoreGMM = 0
for i in range(0,len(results)):
    if results[i] == 1 and y_test[i] == 'chant':
        scoreGMM += 1
    if results[i] == 0 and y_test[i] == 'rap':
        scoreGMM += 1

scoreGMM = scoreGMM / len(results)

print("GMM accuracy: " + str(scoreGMM * 100))

GMM accuracy: 97.6068376068376


In [12]:
# Save models for future testing
joblib.dump(SVM, "models/svm_classifier")
joblib.dump(gmm, "models/gmm_classifier")

['models/gmm_classifier']